In [36]:
import rasterio
import matplotlib.pyplot as plt
import plotly.graph_objects as go
import pandas as pd
import numpy as np
import plotly.io as pio
import plotly.colors as plotly_colors
import geopandas as gpd
from shapely.geometry import mapping
from rasterio import mask as msk
import plotly.graph_objects as go
import dash
import dash_core_components as dcc
import dash_html_components as html
from dash.dependencies import Input, Output
import gunicorn
from whitenoise import WhiteNoise   #for serving static files on Heroku

In [14]:
#!pip install 

In [15]:
#file = rasterio.open('30N090W_20101117_gmted_bln075.tif')
file = rasterio.open('30N090W_20101117_gmted_bln300.tif')
dataset = file.read()[0]

In [16]:
#plt.imshow(dataset, cmap='Spectral')
#plt.show()

In [18]:
df = gpd.read_file('ne_50m_admin_1_states_provinces/ne_50m_admin_1_states_provinces.shp')
ma = df[df['iso_3166_2'] == 'US-MA']
clipped_array, clipped_transform = msk.mask(file, [mapping(ma.iloc[0].geometry)], crop=True)

def clip_raster(gdf, img):
     clipped_array, clipped_transform = msk.mask(img, [mapping(gdf.iloc[0].geometry)], crop=True)
     clipped_array, clipped_transform = msk.mask(img, [mapping(gdf.iloc[0].geometry)],
                                                           crop=True, nodata=0)#(np.amax(clipped_array[0]) + 1))
     clipped_array[0] = clipped_array[0] + abs(np.amin(clipped_array))
     value_range = np.amax(clipped_array) + abs(np.amin(clipped_array))
     return clipped_array, value_range

ma_topography, value_range = clip_raster(ma, file)

"""
plt.figure(figsize=(10,10))
c = plt.imshow(ma_topography[0], cmap='Spectral')
plt.colorbar(c)
plt.show()
"""

"\nplt.figure(figsize=(10,10))\nc = plt.imshow(ma_topography[0], cmap='Spectral')\nplt.colorbar(c)\nplt.show()\n"

In [19]:
#dataset = dataset[0]  # Extract the 2D array from the (1, 2400, 3600) shape

dataset = ma_topography[0]

# Create X and Y coordinate arrays
x = np.arange(dataset.shape[1])
y = np.arange(dataset.shape[0])
x, y = np.meshgrid(x, y)

# Reshape the dataset to match the X and Y coordinate shape
z = dataset.reshape(dataset.shape[0], dataset.shape[1])

"""
# Create the 3D surface plot
fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')
ax.plot_surface(x, y, z)

# Customize the plot if needed
ax.set_xlabel('X')
ax.set_ylabel('Y')
ax.set_zlabel('Z')

# Display the plot
plt.show()
"""


"\n# Create the 3D surface plot\nfig = plt.figure()\nax = fig.add_subplot(111, projection='3d')\nax.plot_surface(x, y, z)\n\n# Customize the plot if needed\nax.set_xlabel('X')\nax.set_ylabel('Y')\nax.set_zlabel('Z')\n\n# Display the plot\nplt.show()\n"

In [43]:
fig = go.Figure(data=[go.Surface(
    z=z, x=x, y=y,
    colorscale='Spectral',
    reversescale=True,
    surfacecolor=[np.sqrt(zval) for zval in z],)])
fig.update_layout(
    #width='auto',
    height=800,
    scene = dict(
        zaxis = dict(nticks=10, range=[0,5000/3],),
        xaxis = dict(nticks=4, range=[0,1715*1.6/5],),
        yaxis = dict(nticks=4, range=[-(784/1.4)/5,784/5],),
        camera_eye = {"x": -0.3, "y": -0.8, "z": 0.5},
        #camera_center=dict(x=1000, y=350, z=0.1),
        aspectratio = {"x": 8, "y": 8, "z": 1}),
    margin=dict(r=20, l=10, b=10, t=10))
#fig.show()
fig.update_layout(template="plotly_white")
#fig.write_html('test2.html')

In [44]:
app = dash.Dash()

# Reference the underlying flask app (Used by gunicorn webserver in Heroku production deployment)
server = app.server 

# Enable Whitenoise for serving static files from Heroku (the /static folder is seen as root by Heroku) 
server.wsgi_app = WhiteNoise(server.wsgi_app, root='static/') 

app.layout = html.Div([
    html.Div([
        #html.H1("Marina Findr"),
        dash.html.Img(src='branding/logo.png'),
        html.P("Unlock exclusive waterfront opportunities as sea levels rise due to climate change. Discover ideal yacht docking spots, secure luxurious summer homes, and strategize your trust fund for generations. Sail to success with Marina Findr, the ultimate web app for embracing the changing world. A rising tide may not raise all boats, but it can certainly raise yours!"),
    ], style={'width': '80%', 'max-width':'800px', 'margin': '0 auto'}),
    html.Div(id='output'),
    html.Div([dcc.Graph(id="fig", figure=fig)], style={'width': '100%', 'height':'100%', 'display': 'inline-block'})
])

@app.callback(
    Output("output","children"),
    Input("fig", "relayoutData")
)
def show_data(data):
    return [str(data)]

#app.run_server(debug=True, use_reloader=False)  # Turn off reloader if inside Jupyter

if __name__ == "__main__": app.run_server(debug=False, host='0.0.0.0', port=8050)


Dash is running on http://0.0.0.0:8050/

 * Serving Flask app '__main__'
 * Debug mode: off


/Users/janeadams/projects/marina-finder/marina/lib/python3.9/site-packages/whitenoise/base.py:109: UserWarning:

No directory at: /Users/janeadams/projects/marina-finder/static/

 * Running on all addresses (0.0.0.0)
 * Running on http://127.0.0.1:8050
 * Running on http://10.50.202.168:8050
Press CTRL+C to quit
127.0.0.1 - - [27/May/2023 17:17:51] "GET / HTTP/1.1" 200 -
127.0.0.1 - - [27/May/2023 17:17:51] "GET /assets/styles.css?m=1685219958.7243624 HTTP/1.1" 200 -
127.0.0.1 - - [27/May/2023 17:17:51] "GET /_dash-component-suites/dash/deps/polyfill@7.v2_10_0m1685204884.12.1.min.js HTTP/1.1" 200 -
127.0.0.1 - - [27/May/2023 17:17:51] "GET /_dash-component-suites/dash/deps/react@16.v2_10_0m1685204884.14.0.min.js HTTP/1.1" 200 -
127.0.0.1 - - [27/May/2023 17:17:51] "GET /_dash-component-suites/dash/deps/react-dom@16.v2_10_0m1685204884.14.0.min.js HTTP/1.1" 200 -
127.0.0.1 - - [27/May/2023 17:17:51] "GET /_dash-component-suites/dash/deps/prop-types@15.v2_10_0m1685204884.8.1.min.js HTTP/1